# Heatmap of Car breakins in San Francisco

Let's load the police data again and extract the car break-ins, which is when the `Incident Subcategory` is `Larceny - From Vehicle`. We can also restrict the time if we want.  Here's how we load the data and filter:

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np

%config InlineBackend.figure_format = 'retina'

In [2]:
df = pd.read_csv("/tmp/SFPD.csv")

df = df[df['Incident Subcategory'] == 'Larceny - From Vehicle']
df['Incident Date'] = pd.to_datetime(df['Incident Date'])
# On comment if you like to restrict two recent times
#df = df[df['Incident Date'] > '01/01/2021']

We also want to get a count associated with each GPS coordinate:

In [3]:
df_ = df.groupby(['Latitude','Longitude']).count().reset_index()
df = df_[['Latitude','Longitude','Incident Date']]
df.columns = ['Latitude','Longitude','count']
print(df.head(5))
lat, long, count = df['Latitude'], df['Longitude'], df['count']

    Latitude   Longitude  count
0  37.707988 -122.462313      1
1  37.708020 -122.412497      1
2  37.708058 -122.441986      1
3  37.708311 -122.420083      1
4  37.708328 -122.449847      1


Then, using Folium, create a map focused on San Francisco zoomed in a bit:

In [4]:
import folium

map = folium.Map(location=[37.779992, -122.413487], zoom_start=13)
map

Now, add a circular marker for each location whose radius is the number of incidents divided by 20 (to scale things):

In [5]:
for a,b,c in zip(lat,long,count):
    if np.isnan(a) or np.isnan(b):
        continue
    folium.CircleMarker([a,b],
                        radius=c/20,
                        weight=1, fill=False).add_to(map)
    
map

That works reasonably well and we can see some of the areas where cars get broken into, but it would be better to use color rather than radius so that the hotspots stick out.

In [10]:
from folium.plugins import HeatMap

map = folium.Map(location=[37.779992, -122.413487], zoom_start=13)
HeatMap(df[['Latitude','Longitude']],
       radius=5,
#        min_opacity=.1,
        blur=1,
       gradient=None).add_to(map)
map

The hotspots seem to be the tourist areas like fisherman's wharf and North Beach, but the tenderloin and Civic Center look pretty bad as well.